In [1]:
import numpy as np
import json
import glob
from sklearn.metrics import pairwise_distances
from matplotlib import pyplot as plt
from collections import defaultdict
import tqdm 
from Bio.PDB import PDBParser
import warnings
import pickle
import dfs_code
import proteingraph as pg
import networkx as nx
from ml_collections import ConfigDict
warnings.filterwarnings('ignore')

In [2]:
from functools import partial
from graphein.protein.config import ProteinGraphConfig
from graphein.protein.graphs import construct_graph
from graphein.protein.edges.distance import (add_peptide_bonds,
                                             add_hydrophobic_interactions,
                                             add_hydrogen_bond_interactions,
                                             add_disulfide_interactions,
                                             add_ionic_interactions,
                                             add_aromatic_interactions,
                                             add_aromatic_sulphur_interactions,
                                             add_cation_pi_interactions
                                            )
from graphein.protein.edges.distance import add_distance_threshold
from graphein.protein.resi_atoms import RESI_THREE_TO_1, AMINO_ACIDS

To use the Graphein submodule graphein.protein.features.sequence.embeddings, you need to install biovec.

To do so, use the following command:

    pip install biovec
To use the Graphein submodule graphein.protein.visualisation, you need to install pytorch3d.

pytorch3d cannot be installed via pip
To use the Graphein submodule graphein.protein.meshes, you need to install pytorch3d.

pytorch3d cannot be installed via pip


In [3]:
path = "/mnt/ssd/datasets/enzyme/"
node_limit = 200# np.inf
min_seq_dist = 2
cutoff = 4.5 # 8 also works

pdb_files = set(glob.glob(path+"pdb_files/*/*.pdb"))
pdb_files_fixed = set(glob.glob(path+"pdb_files/*/*_fixed.pdb"))
pdb_fnames = list(pdb_files - pdb_files_fixed)
pdb_fnames = list(pdb_files_fixed)

In [4]:
aa2int = {aa: idx for idx, aa in enumerate(AMINO_ACIDS)}

In [5]:
bond2bit = {"peptide_bond":0, "hydrophobic":1, "disulfide": 2, "hbond": 3, "ionic": 4, "aromatic": 5, 
            "aromatic_sulphur": 6, "cation_pi" : 7, "distance_threshold": 8}

In [6]:
new_edge_funcs = {"edge_construction_functions": [add_peptide_bonds,
                                                  #add_hydrophobic_interactions,
                                                  #add_hydrogen_bond_interactions,
                                                  #add_disulfide_interactions,
                                                  #add_ionic_interactions,
                                                  #add_aromatic_sulphur_interactions,
                                                  #add_cation_pi_interactions]
                                                  partial(add_distance_threshold, long_interaction_threshold=min_seq_dist, threshold=cutoff)]
                 }
config = ProteinGraphConfig(**new_edge_funcs)
config.dict()

{'granularity': 'CA',
 'keep_hets': False,
 'insertions': False,
 'pdb_dir': PosixPath('../examples/pdbs'),
 'verbose': False,
 'exclude_waters': True,
 'deprotonate': False,
 'protein_df_processing_functions': None,
 'edge_construction_functions': [<function graphein.protein.edges.distance.add_peptide_bonds(G: 'nx.Graph') -> 'nx.Graph'>,
  functools.partial(<function add_distance_threshold at 0x7f4768a1df70>, long_interaction_threshold=2, threshold=4.5)],
 'node_metadata_functions': [<function graphein.protein.features.nodes.amino_acid.meiler_embedding(n, d, return_array: bool = False) -> Union[pandas.core.series.Series, <built-in function array>]>],
 'edge_metadata_functions': None,
 'graph_metadata_functions': None,
 'get_contacts_config': None,
 'dssp_config': None}

In [7]:
def pg2mine(g, aa2int=aa2int, bond2bit=bond2bit):
    edge_index = []
    edge_labels = []
    node_labels = []
    pos = []
    feats = []
    node2idx = {}
    for idx, n in enumerate(g.nodes):
        node_labels.append(aa2int[RESI_THREE_TO_1[g.nodes[n]['residue_name']]])
        pos.append(g.nodes[n]['coords'])
        feats.append(g.nodes[n]['meiler'].to_numpy().tolist() + [g.nodes[n]['b_factor']])
        node2idx[n] = idx
    
    for n in g.nodes:
        for n2, kdict in g[n].items():
            edge_index.append((node2idx[n], node2idx[n2]))
            elabel = 0
            for etype in kdict['kind']:
                elabel += 2**bond2bit[etype]
            edge_labels.append(elabel)
    
    edge_index = np.asarray(edge_index).T
    #min_dfs_code, min_dfs_index = dfs_code.min_dfs_code_from_edgeindex(edge_index, 
    #                                                                   node_labels, 
    #                                                                   edge_labels)
    d = {}
    d['edge_index'] = edge_index
    d['edge_types'] = np.asarray(edge_labels)
    d['node_types'] = np.asarray(node_labels)
    #d['min_dfs_code'] = min_dfs_code
    #d['min_dfs_index'] = min_dfs_index
    d['pos'] = np.asarray(pos)
    d['feats'] = np.asarray(feats)
    return ConfigDict(d)

In [8]:
g = construct_graph(config=config, pdb_code="1dp4")

DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 854 total nodes
DEBUG:graphein.protein.features.nodes.amino_acid:Reading meiler embeddings from: /home/chrisw/.cache/pypoetry/virtualenvs/graph-transformer-9jPERXQ--py3.8/lib/python3.8/site-packages/graphein/protein/features/nodes/meiler_embeddings.csv


In [9]:
d = pg2mine(g)

In [10]:
min_dfs_code, min_dfs_index = dfs_code.min_dfs_code_from_edgeindex(d.edge_index, 
                                                                   d.node_types.tolist(), 
                                                                   d.edge_types.tolist())
d['min_dfs_code'] = min_dfs_code
d['min_dfs_index'] = min_dfs_index

In [11]:
len(d.min_dfs_code)

889

In [12]:
with open(path+"metadata/function_labels.json", "r") as f:
    labels = json.load(f)

In [13]:
with open(path+"metadata/base_split.json", "r") as f:
    split = json.load(f)

In [14]:
len(d['edge_index'].T)

1778

In [15]:
len(d['pos'])

854

In [ ]:
graphs = {}
for fname in tqdm.tqdm(pdb_fnames):
    #try:
    name = fname.split('/')[-2]#[:-2]
    g = construct_graph(config=config, pdb_path=fname)#pdb_code=name)
    graphs[name] = pg2mine(g)
    #except:
    #    continue

  0%|                                                                                                                                                                                    | 0/37427 [00:00<?, ?it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 23 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 147 total nodes
  0%|                                                                                                                                                                            | 2/37427 [00:00<36:47, 16.95it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 262 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein

DEBUG:graphein.protein.graphs:Detected 278 total nodes
  0%|▏                                                                                                                                                                          | 32/37427 [00:02<57:02, 10.92it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 262 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 219 total nodes
  0%|▏                                                                                                                                                                          | 34/37427 [00:03<54:36, 11.41it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 122 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This 

DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 449 total nodes
  0%|▎                                                                                                                                                                        | 64/37427 [00:05<1:06:39,  9.34it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 552 total nodes
  0%|▎                                                                                                                                                                        | 65/37427 [00:06<1:11:10,  8.75it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 433 total nodes
  0%|▎                                                                                                           

  0%|▍                                                                                                                                                                          | 93/37427 [00:08<46:39, 13.33it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 341 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 491 total nodes
  0%|▍                                                                                                                                                                          | 95/37427 [00:08<53:25, 11.65it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 219 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphei

DEBUG:graphein.protein.graphs:Detected 277 total nodes
  0%|▌                                                                                                                                                                         | 125/37427 [00:11<57:06, 10.89it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 327 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 322 total nodes
  0%|▌                                                                                                                                                                       | 127/37427 [00:11<1:04:54,  9.58it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 347 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This 

...

DEBUG:graphein.protein.graphs:Detected 393 total nodes
 74%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉                                           | 27828/37427 [44:15<17:08,  9.34it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 330 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 288 total nodes
 74%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉                                           | 27830/37427 [44:15<16:29,  9.70it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 174 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This 

DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 87 total nodes
 74%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████                                           | 27860/37427 [44:18<14:01, 11.37it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 309 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 262 total nodes
 74%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████                                           | 27862/37427 [44:18<14:02, 11.35it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein

DEBUG:graphein.protein.graphs:Detected 222 total nodes
 75%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                          | 27891/37427 [44:21<15:43, 10.11it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 691 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 873 total nodes
 75%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                          | 27893/37427 [44:22<20:45,  7.65it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 274 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This 

 75%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎                                          | 27921/37427 [44:24<16:23,  9.67it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 119 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 308 total nodes
 75%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎                                          | 27923/37427 [44:25<14:59, 10.57it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 34 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein

 75%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍                                          | 27949/37427 [44:28<20:40,  7.64it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 326 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 50 total nodes
 75%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍                                          | 27951/37427 [44:28<16:55,  9.33it/s]DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein.protein.graphs:Detected 164 total nodes
DEBUG:graphein.protein.graphs:Deprotonating protein. This removes H atoms from the pdb_df dataframe
DEBUG:graphein

In [ ]:
with open(path+'graphein_basic.pkl', 'wb') as f:
    pickle.dump(graphs, f)

In [ ]:
print(len(graphs) == len(pdb_fnames))

In [ ]:
len(graphs)

In [ ]:
len(pdb_fnames)